In [11]:
import pandas as pd  
import numpy as np  
import xgboost as xgb  

from sklearn.metrics import mean_squared_error
from xgboost.sklearn import XGBClassifier  
from sklearn.model_selection import GridSearchCV,cross_val_score  
from sklearn import  metrics  
import matplotlib.pylab as plt  

In [12]:
train_df = pd.read_csv('train.csv')  
test_df = pd.read_csv('test.csv') 
print(train_df)

        时间   小区名  小区房屋出租数量  楼层       总楼层      房屋面积 房屋朝向  居住状态  卧室数量  厅的数量  \
0        1  3072  0.128906   2  0.236364  0.008628   东南   NaN     1     1   
1        1  3152  0.132812   1  0.381818  0.017046    东   NaN     1     0   
2        1  5575  0.042969   0  0.290909  0.010593   东南   NaN     2     1   
3        1  3103  0.085938   2  0.581818  0.019199    南   NaN     3     2   
4        1  5182  0.214844   0  0.545455  0.010427   东北   NaN     2     1   
5        1  1192  0.039062   2  0.309091  0.012579    南   NaN     2     1   
6        1  1122  0.125000   0  0.381818  0.010593    南   NaN     3     1   
7        1  1251  0.128906   2  0.363636  0.018040    南   NaN     4     2   
8        1  4718  0.246094   2  0.309091  0.007850   西南   NaN     1     1   
9        1  2654  0.218750   2  0.890909  0.020026   东南   NaN     2     1   
10       1  4847  0.042969   2  0.272727  0.010096  南 北   NaN     2     2   
11       1  3069  0.031250   1  0.272727  0.031034    南   NaN     1     0   

In [10]:
 
train_df.rename(columns={'时间':'time', '小区名':'community', '小区房屋出租数量':'house_num', '楼层':'floor', '总楼层':'total_floor', '房屋面积':'area', '房屋朝向':'orientation', '居住状态':'status', '卧室数量':'bedroom_num',
       '厅的数量':'livingroom_num', '卫的数量':'bathroom_num', '出租方式':'method', '区':'Urban', '位置':'location', '地铁线路':'underground', '地铁站点':'underground_station', '距离':'distance', '装修情况':'Decoration', '月租金':'price'},inplace=True)
test_df.rename(columns={'时间':'time', '小区名':'community', '小区房屋出租数量':'house_num', '楼层':'floor', '总楼层':'total_floor', '房屋面积':'area', '房屋朝向':'orientation', '居住状态':'status', '卧室数量':'bedroom_num',
       '厅的数量':'livingroom_num', '卫的数量':'bathroom_num', '出租方式':'method', '区':'Urban', '位置':'location', '地铁线路':'underground', '地铁站点':'underground_station', '距离':'distance', '装修情况':'Decoration'},inplace=True)

In [4]:
train_df.drop(['distance','status','method','time','underground','underground_station','Decoration'],axis=1,inplace=True)# 删除缺省值过多项
test_df.drop(['distance','status','method','time','underground','underground_station','Decoration'],axis=1,inplace=True)# 删除缺省值过多项

In [3]:
quantity = [attr for attr in train_df.columns if train_df.dtypes[attr] != 'object']  # 数值变量集合
quality = [attr for attr in train_df.columns if train_df.dtypes[attr] == 'object'] 

In [4]:
def encode(frame,test, feature):
    '''
    对所有类型变量，依照各个类型变量的不同取值对应的样本集内房价的均值，按照房价均值高低
    对此变量的当前取值确定其相对数值1,2,3,4等等，相当于对类型变量赋值使其成为连续变量。
    此方法采用了与One-Hot编码不同的方法来处理离散数据，值得学习
    注意：此函数会直接在原frame的DataFrame内创建新的一列来存放feature编码后的值。
    '''
    ordering = pd.DataFrame()
    ordering['val'] = frame[feature].unique()
    ordering.index = ordering.val
    ordering['price_mean'] = frame[[feature, 'price']].groupby(feature).mean()['price']
    # 上述 groupby()操作可以将某一feature下同一取值的数据整个到一起，结合mean()可以直接得到该特征不同取值的房价均值
    ordering = ordering.sort_values('price_mean')
    ordering['order'] = range(1, ordering.shape[0]+1)
    ordering = ordering['order'].to_dict()
    for attr_v, score in ordering.items():
        # e.g. qualitative[2]: {'Grvl': 1, 'MISSING': 3, 'Pave': 2}
        frame.loc[frame[feature] == attr_v, feature+'_E'] = score
        test_df.loc[test_df[feature] == attr_v, feature+'_E'] = score

quality_encoded = []
# 由于qualitative集合中包含了非数值型变量和伪数值型变量（多为评分、等级等，其取值为1,2,3,4等等）两类
# 因此只需要对非数值型变量进行encode()处理。
# 如果采用One-Hot编码，则整个qualitative的特征都要进行pd,get_dummies()处理
for q in quality:
    encode(train_df,test_df, q)
    quality_encoded.append(q+'_E')
train_df.drop(quality, axis=1, inplace=True)
test_df.drop(quality, axis=1, inplace=True) # 离散变量已经有了编码后的新变量，因此删去原变量
# df_tr.shape = (1460, 80)
print(quality_encoded, '\n{} qualitative attributes have been encoded.'.format(len(quality_encoded)))

['orientation_E'] 
1 qualitative attributes have been encoded.


In [7]:
train_df.drop(['location','community','floor','house_num'],axis=1,inplace=True)
test_df.drop(['location','community','floor','house_num'],axis=1,inplace=True)

In [6]:
train_df=train_df[(train_df['area']<0.10)]#离散点处理 待改进

In [6]:
train_y = train_df.price 
train_X = train_df.drop(['price'],axis=1) 
test_df.drop('id',axis=1,inplace=True)  

In [7]:
def modelMetrics(clf,train_x,train_y,isCv=True,cv_folds=5,early_stopping_rounds=50):  
    if isCv:  
        xgb_param = clf.get_xgb_params()  
        xgb_param['tree_method']='gpu_hist'
        xgtrain = xgb.DMatrix(train_x,label=train_y)  
        cvresult = xgb.cv(xgb_param,xgtrain,num_boost_round=clf.get_params()['n_estimators'],nfold=cv_folds,  
                          metrics='rmse',early_stopping_rounds=early_stopping_rounds,verbose_eval=True)#是否显示目前几颗树额  
        clf.set_params(n_estimators=cvresult.shape[0])  
  
    clf.fit(train_x,train_y,eval_metric='rmse')  
  
    #预测  
    train_predictions = clf.predict(train_x)  
  
    #打印  
    print("\nModel Report")  
    print(mean_squared_error(train_y,train_predictions)**0.5)  
  
    feat_imp = pd.Series(clf.booster().get_fscore()).sort_values(ascending=False)  
    feat_imp.plot(kind='bar',title='Feature importance')  
    plt.ylabel('Feature Importance Score')  

In [8]:
xgb1 = XGBClassifier(learning_rate = 0.3, n_estimators = 3500, max_depth = 5, gamma = 0, subsample = 0.8,
        colsample_bytree = 0.8, objective = 'reg:linear', nthread = 4,  seed = 27,scoring='neg_mean_squared_error',verbose=True,iid=True)

In [7]:
#xgb_param = xgb1.get_xgb_params()  
params = {'objective':'reg:linear','eval_metric':'rmse' }
xgtrain = xgb.DMatrix(train_X,label=train_y)  
cvresult = xgb.cv(params,xgtrain,num_boost_round=20000,nfold=5,  
                          metrics='rmse',early_stopping_rounds=50)#是否显示目前几颗树额  
#xgb1.set_params(n_estimators=cvresult
print(cvresult.shape[0])
#xgb1.fit(train_X,train_y,eval_metric='rmse') 
#train_predictions = xgb1.predict(train_X) 
#print(mean_squared_error(train_y,train_predictions)**0.5)  
xgb_param = {'objective':'reg:linear','eval_metric':'rmse' }

xgtest = xgb.DMatrix(test_df)
watchlist=[(xgtrain,'train')]

bst=xgb.train(xgb_param,dtrain=xgtrain,num_boost_round=cvresult.shape[0],early_stopping_rounds=50,evals=watchlist)
test_predictions = bst.predict(xgtest) 

[03:53:34] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 126 extra nodes, 0 pruned nodes, max_depth=6
[03:53:35] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 0 pruned nodes, max_depth=6
[03:53:35] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 126 extra nodes, 0 pruned nodes, max_depth=6
[03:53:35] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 126 extra nodes, 0 pruned nodes, max_depth=6
[03:53:35] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 0 pruned nodes, max_depth=6
[03:53:35] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 126 extra nodes, 0 pruned nodes, max_depth=6
[03:53:35] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 126 extra nodes,

[03:53:36] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=6
[03:53:36] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=6
[03:53:36] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[03:53:36] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 104 extra nodes, 0 pruned nodes, max_depth=6
[03:53:36] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 104 extra nodes, 0 pruned nodes, max_depth=6
[03:53:36] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=6
[03:53:36] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 82 extra nodes, 

[03:53:38] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[03:53:38] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=6
[03:53:38] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=6
[03:53:38] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 112 extra nodes, 0 pruned nodes, max_depth=6
[03:53:38] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 76 extra nodes, 0 pruned nodes, max_depth=6
[03:53:38] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[03:53:38] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 

[03:53:40] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 42 extra nodes, 0 pruned nodes, max_depth=6
[03:53:40] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 96 extra nodes, 0 pruned nodes, max_depth=6
[03:53:40] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=6
[03:53:40] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=6
[03:53:40] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=6
[03:53:40] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=6
[03:53:40] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 68 extra nodes, 0 

[03:53:41] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=6
[03:53:41] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 100 extra nodes, 0 pruned nodes, max_depth=6
[03:53:42] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 96 extra nodes, 0 pruned nodes, max_depth=6
[03:53:42] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 96 extra nodes, 0 pruned nodes, max_depth=6
[03:53:42] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[03:53:42] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 82 extra nodes, 0 pruned nodes, max_depth=6
[03:53:42] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 102 extra nodes, 0 

...

[04:10:51] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=6
[5589]	train-rmse:0.50341
[04:10:51] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 120 extra nodes, 0 pruned nodes, max_depth=6
[5590]	train-rmse:0.503392
[04:10:51] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 0 pruned nodes, max_depth=6
[5591]	train-rmse:0.50336
[04:10:51] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[5592]	train-rmse:0.503303
[04:10:51] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[5593]	train-rmse:0.503231
[04:10:51] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned node

[04:10:53] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=6
[5637]	train-rmse:0.501363
[04:10:53] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 120 extra nodes, 0 pruned nodes, max_depth=6
[5638]	train-rmse:0.501303
[04:10:53] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=6
[5639]	train-rmse:0.501288
[04:10:53] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 104 extra nodes, 0 pruned nodes, max_depth=6
[5640]	train-rmse:0.501261
[04:10:53] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 102 extra nodes, 0 pruned nodes, max_depth=6
[5641]	train-rmse:0.501244
[04:10:53] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 116 extra nodes, 0 pruned no

[04:10:54] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 0 pruned nodes, max_depth=6
[5685]	train-rmse:0.499771
[04:10:55] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 94 extra nodes, 0 pruned nodes, max_depth=6
[5686]	train-rmse:0.499751
[04:10:55] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=6
[5687]	train-rmse:0.499733
[04:10:55] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[5688]	train-rmse:0.499678
[04:10:55] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 102 extra nodes, 0 pruned nodes, max_depth=6
[5689]	train-rmse:0.499667
[04:10:55] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 114 extra nodes, 0 pruned nod

[04:10:56] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=6
[5733]	train-rmse:0.498265
[04:10:56] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=6
[5734]	train-rmse:0.49821
[04:10:56] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 112 extra nodes, 0 pruned nodes, max_depth=6
[5735]	train-rmse:0.498142
[04:10:56] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=6
[5736]	train-rmse:0.498095
[04:10:56] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 106 extra nodes, 0 pruned nodes, max_depth=6
[5737]	train-rmse:0.498082
[04:10:56] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 72 extra nodes, 0 pruned node

[04:10:58] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 106 extra nodes, 0 pruned nodes, max_depth=6
[5781]	train-rmse:0.496893
[04:10:58] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 114 extra nodes, 0 pruned nodes, max_depth=6
[5782]	train-rmse:0.496863
[04:10:58] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=6
[5783]	train-rmse:0.496848
[04:10:58] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 120 extra nodes, 0 pruned nodes, max_depth=6
[5784]	train-rmse:0.496818
[04:10:58] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 114 extra nodes, 0 pruned nodes, max_depth=6
[5785]	train-rmse:0.496807
[04:10:58] d:\build\xgboost\xgboost-0.81.git\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned no

In [9]:
#xgb_param = xgb1.get_xgb_params()  
params = {'objective':'reg:linear','eval_metric':'rmse' }
xgtrain = xgb.DMatrix(train_X,label=train_y)  
sult = xgb.cv(params,xgtrain,num_boost_round=50,nfold=5,verbose_eval=True , 
                          metrics='rmse',early_stopping_rounds=50,seed=27)

[21:52:43] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 0 pruned nodes, max_depth=6
[21:52:43] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[21:52:43] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 0 pruned nodes, max_depth=6
[21:52:44] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 0 pruned nodes, max_depth=6
[21:52:44] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 126 extra nodes, 0 pruned nodes, max_depth=6
[0]	train-rmse:7.39107+0.0094984	test-rmse:7.40224+0.0372174
[21:52:44] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 126 extra nodes, 0 pruned nodes, max_depth=6
[21:52:44] C:\Users\Adminis

[21:52:48] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 98 extra nodes, 0 pruned nodes, max_depth=6
[21:52:48] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 114 extra nodes, 0 pruned nodes, max_depth=6
[21:52:48] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 106 extra nodes, 0 pruned nodes, max_depth=6
[21:52:48] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 112 extra nodes, 0 pruned nodes, max_depth=6
[21:52:48] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 116 extra nodes, 0 pruned nodes, max_depth=6
[10]	train-rmse:3.02744+0.0239617	test-rmse:3.12987+0.0288471
[21:52:48] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 102 extra nodes, 0 pruned nodes, max_depth=6
[21:52:48] C:\Users\Adminis

[21:52:52] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=6
[21:52:52] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 106 extra nodes, 0 pruned nodes, max_depth=6
[21:52:52] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=6
[21:52:52] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 98 extra nodes, 0 pruned nodes, max_depth=6
[21:52:52] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 96 extra nodes, 0 pruned nodes, max_depth=6
[20]	train-rmse:2.70558+0.0108635	test-rmse:2.83502+0.037551
[21:52:52] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 124 extra nodes, 0 pruned nodes, max_depth=6
[21:52:52] C:\Users\Administr

[21:52:56] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 104 extra nodes, 0 pruned nodes, max_depth=6
[21:52:56] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 98 extra nodes, 0 pruned nodes, max_depth=6
[21:52:56] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 92 extra nodes, 0 pruned nodes, max_depth=6
[21:52:56] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 76 extra nodes, 0 pruned nodes, max_depth=6
[21:52:57] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=6
[30]	train-rmse:2.52763+0.0281388	test-rmse:2.67352+0.0466934
[21:52:57] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 86 extra nodes, 0 pruned nodes, max_depth=6
[21:52:57] C:\Users\Administra

[21:53:00] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 100 extra nodes, 0 pruned nodes, max_depth=6
[21:53:01] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 88 extra nodes, 0 pruned nodes, max_depth=6
[21:53:01] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 92 extra nodes, 0 pruned nodes, max_depth=6
[21:53:01] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 88 extra nodes, 0 pruned nodes, max_depth=6
[21:53:01] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 126 extra nodes, 0 pruned nodes, max_depth=6
[40]	train-rmse:2.39785+0.0247913	test-rmse:2.56662+0.0382992
[21:53:01] C:\Users\Administrator\Desktop\xgboost\src\tree\updater_prune.cc:74: tree pruning end, 1 roots, 58 extra nodes, 0 pruned nodes, max_depth=6
[21:53:01] C:\Users\Administra

In [19]:
print(sult.iloc[-1]['test-rmse-mean'])

2.4782038


In [8]:
select=[];
best=[];
xgtrain = xgb.DMatrix(train_X,label=train_y)
for i in range(9,12,1):
    for j in range(4,8,1):
        select.append((i,j))
for i in select:
    params = {'objective':'reg:linear','eval_metric':'rmse' ,'max_depth':i[0],'min_child_weight':i[1],'tree_method':'gpu_hist'}
    sult = xgb.cv(params,xgtrain,num_boost_round=20000,nfold=5,verbose_eval=True , 
                          metrics='rmse',early_stopping_rounds=50,seed=27)
    best.append(i)
    best.append(sult.iloc[-1]['test-rmse-mean'])
  
                    

XGBoostError: b'[18:35:51] C:/Users/Administrator/Desktop/xgboost/src/tree/updater_gpu_hist.cu:908: Exception in gpu_hist: [18:35:51] c:\\users\\administrator\\desktop\\xgboost\\src\\common\\device_helpers.cuh:854: Check failed: device_ordinals.size() == 1 (0 vs. 1) XGBoost must be compiled with NCCL to use more than one GPU.\n'

In [10]:
params = {'objective':'reg:linear','eval_metric':'rmse','tree_method':'gpu_hist'}
sult = xgb.cv(params,xgtrain,num_boost_round=20000,nfold=5,verbose_eval=True , 
                          metrics='rmse',early_stopping_rounds=50,seed=27)

[0]	train-rmse:7.3975+0.00815001	test-rmse:7.41132+0.0389553
[1]	train-rmse:5.82885+0.0109848	test-rmse:5.85268+0.0311438
[2]	train-rmse:4.82783+0.0115757	test-rmse:4.86212+0.0306515
[3]	train-rmse:4.19788+0.0150544	test-rmse:4.24252+0.0256352
[4]	train-rmse:3.80067+0.00718323	test-rmse:3.85494+0.0402953
[5]	train-rmse:3.55313+0.0141134	test-rmse:3.61917+0.0517167
[6]	train-rmse:3.38746+0.0207973	test-rmse:3.45569+0.052357
[7]	train-rmse:3.26901+0.0138066	test-rmse:3.34557+0.0441689
[8]	train-rmse:3.17317+0.00876262	test-rmse:3.26125+0.0427205
[9]	train-rmse:3.11474+0.0156802	test-rmse:3.20882+0.0429835
[10]	train-rmse:3.05736+0.0191622	test-rmse:3.15875+0.0418558
[11]	train-rmse:3.0086+0.0197927	test-rmse:3.11571+0.0537191
[12]	train-rmse:2.97353+0.0136504	test-rmse:3.08481+0.0454919
[13]	train-rmse:2.93007+0.0108487	test-rmse:3.04426+0.0424288
[14]	train-rmse:2.89945+0.0137999	test-rmse:3.01447+0.0406033
[15]	train-rmse:2.87098+0.0116159	test-rmse:2.98779+0.0389381
[16]	train-rmse:2.

[133]	train-rmse:1.85851+0.0040535	test-rmse:2.16645+0.0131783
[134]	train-rmse:1.8559+0.00412768	test-rmse:2.1646+0.0127435
[135]	train-rmse:1.85324+0.00409153	test-rmse:2.16205+0.0130365
[136]	train-rmse:1.84978+0.00418541	test-rmse:2.15909+0.0130483
[137]	train-rmse:1.84721+0.00449952	test-rmse:2.15717+0.0132409
[138]	train-rmse:1.84458+0.00519126	test-rmse:2.15546+0.0129661
[139]	train-rmse:1.84139+0.00491218	test-rmse:2.15293+0.0122015
[140]	train-rmse:1.83793+0.00501515	test-rmse:2.15023+0.0126708
[141]	train-rmse:1.83489+0.00548449	test-rmse:2.1476+0.0137319
[142]	train-rmse:1.8323+0.00639829	test-rmse:2.14535+0.013626
[143]	train-rmse:1.82943+0.00722221	test-rmse:2.14301+0.014213
[144]	train-rmse:1.82627+0.00724311	test-rmse:2.14118+0.0134302
[145]	train-rmse:1.8229+0.00803881	test-rmse:2.13895+0.0144271
[146]	train-rmse:1.82028+0.00661961	test-rmse:2.13634+0.0135502
[147]	train-rmse:1.81723+0.00731752	test-rmse:2.13372+0.0134355
[148]	train-rmse:1.81366+0.00755293	test-rmse:2.

[263]	train-rmse:1.54822+0.00735951	test-rmse:1.93498+0.0153944
[264]	train-rmse:1.54671+0.00776939	test-rmse:1.93401+0.0155914
[265]	train-rmse:1.54572+0.00781349	test-rmse:1.93343+0.0159056
[266]	train-rmse:1.54384+0.00804836	test-rmse:1.93162+0.0172021
[267]	train-rmse:1.54192+0.00841555	test-rmse:1.93013+0.0175684
[268]	train-rmse:1.54103+0.0085917	test-rmse:1.92936+0.0173224
[269]	train-rmse:1.54018+0.00880842	test-rmse:1.92892+0.017086
[270]	train-rmse:1.53951+0.00897996	test-rmse:1.92843+0.0172819
[271]	train-rmse:1.53785+0.00827305	test-rmse:1.92709+0.0172425
[272]	train-rmse:1.53628+0.00810599	test-rmse:1.92633+0.016986
[273]	train-rmse:1.53504+0.007339	test-rmse:1.92511+0.016732
[274]	train-rmse:1.53412+0.00734099	test-rmse:1.92442+0.0163069
[275]	train-rmse:1.5325+0.00767427	test-rmse:1.92305+0.0167747
[276]	train-rmse:1.53062+0.00829688	test-rmse:1.92165+0.016473
[277]	train-rmse:1.52884+0.00859849	test-rmse:1.92051+0.0167543
[278]	train-rmse:1.52757+0.00930845	test-rmse:1.

[393]	train-rmse:1.37831+0.00995312	test-rmse:1.81472+0.0191528
[394]	train-rmse:1.37748+0.0097192	test-rmse:1.81435+0.0191099
[395]	train-rmse:1.37596+0.00970461	test-rmse:1.81269+0.0199039
[396]	train-rmse:1.37531+0.00959172	test-rmse:1.81217+0.0196671
[397]	train-rmse:1.37444+0.00956101	test-rmse:1.81158+0.0195731
[398]	train-rmse:1.3737+0.00951457	test-rmse:1.81115+0.0195234
[399]	train-rmse:1.37264+0.00937287	test-rmse:1.81059+0.0190399
[400]	train-rmse:1.3719+0.00952939	test-rmse:1.81029+0.0191987
[401]	train-rmse:1.37083+0.00959668	test-rmse:1.80957+0.0194168
[402]	train-rmse:1.36934+0.009554	test-rmse:1.8087+0.0196192
[403]	train-rmse:1.36798+0.00958252	test-rmse:1.80784+0.0198452
[404]	train-rmse:1.36601+0.00952858	test-rmse:1.8066+0.0201411
[405]	train-rmse:1.36512+0.00981553	test-rmse:1.80586+0.0203097
[406]	train-rmse:1.36415+0.00940498	test-rmse:1.80505+0.0199291
[407]	train-rmse:1.36301+0.00978459	test-rmse:1.80461+0.0201209
[408]	train-rmse:1.36203+0.009682	test-rmse:1.8

[523]	train-rmse:1.25541+0.0084953	test-rmse:1.73889+0.0219834
[524]	train-rmse:1.25511+0.00856387	test-rmse:1.73876+0.0219784
[525]	train-rmse:1.25465+0.00847796	test-rmse:1.73846+0.0220813
[526]	train-rmse:1.2542+0.00850685	test-rmse:1.73823+0.0220989
[527]	train-rmse:1.25366+0.00844553	test-rmse:1.73783+0.0218694
[528]	train-rmse:1.25283+0.00818436	test-rmse:1.73722+0.0217022
[529]	train-rmse:1.25186+0.00796331	test-rmse:1.73689+0.0217751
[530]	train-rmse:1.2509+0.00791068	test-rmse:1.73631+0.0218226
[531]	train-rmse:1.25013+0.00798449	test-rmse:1.73569+0.0218385
[532]	train-rmse:1.24945+0.00783476	test-rmse:1.73536+0.0219109
[533]	train-rmse:1.24854+0.00814962	test-rmse:1.73468+0.0217486
[534]	train-rmse:1.24749+0.00852706	test-rmse:1.73442+0.0218974
[535]	train-rmse:1.24631+0.00826603	test-rmse:1.73345+0.0220322
[536]	train-rmse:1.2454+0.00829521	test-rmse:1.73296+0.0219972
[537]	train-rmse:1.24465+0.00818894	test-rmse:1.73256+0.0220223
[538]	train-rmse:1.24384+0.00841297	test-rms

...

[4553]	train-rmse:0.572029+0.00759194	test-rmse:1.4447+0.0458386
[4554]	train-rmse:0.571992+0.00758444	test-rmse:1.4447+0.0458384
[4555]	train-rmse:0.571947+0.00759977	test-rmse:1.44468+0.0458368
[4556]	train-rmse:0.571908+0.00761729	test-rmse:1.44466+0.0458311
[4557]	train-rmse:0.571861+0.00759289	test-rmse:1.44466+0.0458199
[4558]	train-rmse:0.571818+0.00758416	test-rmse:1.44466+0.0458419
[4559]	train-rmse:0.571744+0.00759403	test-rmse:1.44465+0.0458279
[4560]	train-rmse:0.571698+0.00759597	test-rmse:1.44463+0.0458214
[4561]	train-rmse:0.571658+0.00759694	test-rmse:1.44464+0.0458234
[4562]	train-rmse:0.571619+0.00760103	test-rmse:1.44462+0.0458184
[4563]	train-rmse:0.571565+0.00762548	test-rmse:1.4446+0.0458247
[4564]	train-rmse:0.571529+0.00762802	test-rmse:1.44461+0.0458106
[4565]	train-rmse:0.57146+0.00758301	test-rmse:1.44458+0.0458317
[4566]	train-rmse:0.571407+0.00755434	test-rmse:1.44457+0.0458094
[4567]	train-rmse:0.571346+0.00754568	test-rmse:1.44454+0.0458216
[4568]	train-r

[4678]	train-rmse:0.566682+0.00767719	test-rmse:1.44369+0.0461107
[4679]	train-rmse:0.566641+0.00767477	test-rmse:1.44368+0.0461158
[4680]	train-rmse:0.566599+0.00768563	test-rmse:1.44368+0.0461616
[4681]	train-rmse:0.566565+0.00768827	test-rmse:1.44368+0.0461534
[4682]	train-rmse:0.566517+0.00769094	test-rmse:1.44368+0.0461522
[4683]	train-rmse:0.566482+0.00768201	test-rmse:1.44367+0.0461626
[4684]	train-rmse:0.56644+0.00767462	test-rmse:1.44366+0.046175
[4685]	train-rmse:0.566392+0.00764664	test-rmse:1.44365+0.0461919
[4686]	train-rmse:0.566356+0.00763204	test-rmse:1.44363+0.0461855
[4687]	train-rmse:0.5663+0.0076262	test-rmse:1.4436+0.0462253
[4688]	train-rmse:0.566245+0.00761955	test-rmse:1.44359+0.0462138
[4689]	train-rmse:0.566205+0.00762486	test-rmse:1.44357+0.0462236
[4690]	train-rmse:0.566164+0.00761922	test-rmse:1.44356+0.0462085
[4691]	train-rmse:0.566119+0.00759776	test-rmse:1.44358+0.0461961
[4692]	train-rmse:0.566081+0.00759912	test-rmse:1.44356+0.0462032
[4693]	train-rms

[4803]	train-rmse:0.561132+0.00774745	test-rmse:1.44267+0.0462397
[4804]	train-rmse:0.561086+0.00773445	test-rmse:1.44269+0.0462168
[4805]	train-rmse:0.561058+0.0077414	test-rmse:1.44267+0.0462263
[4806]	train-rmse:0.561015+0.00775284	test-rmse:1.44269+0.0462181
[4807]	train-rmse:0.560957+0.00774352	test-rmse:1.44267+0.0462167
[4808]	train-rmse:0.560913+0.00775735	test-rmse:1.44266+0.0462068
[4809]	train-rmse:0.56088+0.00776765	test-rmse:1.44264+0.0462085
[4810]	train-rmse:0.560845+0.00778008	test-rmse:1.44262+0.0462151
[4811]	train-rmse:0.560809+0.00778511	test-rmse:1.44261+0.0462134
[4812]	train-rmse:0.560774+0.00777545	test-rmse:1.4426+0.0462128
[4813]	train-rmse:0.560734+0.00776213	test-rmse:1.44258+0.0462109
[4814]	train-rmse:0.560684+0.00775182	test-rmse:1.44255+0.0462026
[4815]	train-rmse:0.560627+0.00773587	test-rmse:1.44256+0.0461897
[4816]	train-rmse:0.560598+0.00772682	test-rmse:1.44255+0.0461952
[4817]	train-rmse:0.560546+0.00771704	test-rmse:1.4426+0.0461792
[4818]	train-r

[4928]	train-rmse:0.556032+0.00790417	test-rmse:1.4417+0.04629
[4929]	train-rmse:0.555987+0.0078982	test-rmse:1.44169+0.0462877
[4930]	train-rmse:0.555943+0.00790618	test-rmse:1.44169+0.0462903
[4931]	train-rmse:0.555916+0.00791075	test-rmse:1.44167+0.0462897
[4932]	train-rmse:0.555885+0.00791276	test-rmse:1.44167+0.0462845
[4933]	train-rmse:0.555826+0.00792458	test-rmse:1.44163+0.046284
[4934]	train-rmse:0.555774+0.00792096	test-rmse:1.44162+0.0463075
[4935]	train-rmse:0.555719+0.0079116	test-rmse:1.4416+0.0462988
[4936]	train-rmse:0.555658+0.00791314	test-rmse:1.44159+0.0463075
[4937]	train-rmse:0.555618+0.00790928	test-rmse:1.44159+0.0463082
[4938]	train-rmse:0.555593+0.00790755	test-rmse:1.44157+0.0463163
[4939]	train-rmse:0.555547+0.00791377	test-rmse:1.44156+0.0463137
[4940]	train-rmse:0.555515+0.00790827	test-rmse:1.44157+0.0463151
[4941]	train-rmse:0.555489+0.00789057	test-rmse:1.44154+0.0463325
[4942]	train-rmse:0.555443+0.00790937	test-rmse:1.44154+0.046325
[4943]	train-rmse:

[5053]	train-rmse:0.551194+0.00779565	test-rmse:1.44096+0.0464593
[5054]	train-rmse:0.551166+0.00779154	test-rmse:1.44096+0.046459
[5055]	train-rmse:0.551144+0.00778285	test-rmse:1.44094+0.0464639
[5056]	train-rmse:0.551072+0.00777382	test-rmse:1.44092+0.0464731
[5057]	train-rmse:0.551041+0.00777341	test-rmse:1.44092+0.0464705
[5058]	train-rmse:0.551014+0.00777666	test-rmse:1.44091+0.0464707
[5059]	train-rmse:0.55099+0.00777608	test-rmse:1.4409+0.0464722
[5060]	train-rmse:0.550953+0.00776325	test-rmse:1.44089+0.0464722
[5061]	train-rmse:0.55093+0.00776871	test-rmse:1.44089+0.0464738
[5062]	train-rmse:0.55091+0.00777761	test-rmse:1.44087+0.0464594
[5063]	train-rmse:0.550875+0.00778061	test-rmse:1.44087+0.0464612
[5064]	train-rmse:0.550819+0.0078072	test-rmse:1.44086+0.0464615
[5065]	train-rmse:0.550763+0.00779212	test-rmse:1.44083+0.0464556
[5066]	train-rmse:0.550743+0.00779318	test-rmse:1.44083+0.0464541
[5067]	train-rmse:0.550719+0.00779646	test-rmse:1.44082+0.0464542
[5068]	train-rms

In [8]:
print(best)

[(9, 4), 1.4214246000000001, (9, 5), 1.4061255999999998, (9, 6), 1.4278518000000002, (9, 7), 1.4182115999999998, (10, 4), 1.4196626, (10, 5), 1.4180312000000002, (10, 6), 1.4280152, (10, 7), 1.425479, (11, 4), 1.4290062000000001, (11, 5), 1.429926, (11, 6), 1.4311774000000002, (11, 7), 1.4328858]


In [ ]:
select=[];
best=[];
xgtrain = xgb.DMatrix(train_X,label=train_y)
for i in range(5,10,2):
    for j in range(1,6,2):
        select.append((i,j))
for i in select:
    params = {'objective':'reg:linear','eval_metric':'rmse' ,'max_depth':i[0],'min_child_weight':i[1],'tree_method':'gpu_hist'}
    sult = xgb.cv(params,xgtrain,num_boost_round=50000,nfold=5,verbose_eval=True , 
                          metrics='rmse',early_stopping_rounds=50,seed=27)
    if best==[]:
        best.append(i)
        best.append(sult.iloc[-1]['test-rmse-mean'])
        print('change',best)
    elif sult.iloc[-1]['test-rmse-mean']<best[1]:
                    best[0]=i
                    best[1]=sult.iloc[-1]['test-rmse-mean']
                    print('change',best)

In [17]:
params = {'objective':'reg:linear','eval_metric':'rmse' ,'max_depth':9,'min_child_weight':5,'tree_method':'gpu_hist'}
sult = xgb.cv(params,xgtrain,num_boost_round=50000,nfold=5,verbose_eval=True , 
                          metrics='rmse',early_stopping_rounds=50,seed=27)

[0]	train-rmse:7.24368+0.012966	test-rmse:7.26736+0.034558
[1]	train-rmse:5.53723+0.0201563	test-rmse:5.58487+0.0275503
[2]	train-rmse:4.40427+0.0182444	test-rmse:4.47772+0.0340351
[3]	train-rmse:3.65541+0.0188281	test-rmse:3.76138+0.0332661
[4]	train-rmse:3.16771+0.0203751	test-rmse:3.30092+0.0395556
[5]	train-rmse:2.86297+0.0247881	test-rmse:3.01281+0.0385369
[6]	train-rmse:2.66008+0.0258784	test-rmse:2.82354+0.0317276
[7]	train-rmse:2.51656+0.0180923	test-rmse:2.69367+0.0203023
[8]	train-rmse:2.4065+0.0152862	test-rmse:2.59525+0.0225502
[9]	train-rmse:2.33709+0.0171878	test-rmse:2.53512+0.0230466
[10]	train-rmse:2.27443+0.0103811	test-rmse:2.48493+0.0274582
[11]	train-rmse:2.22821+0.0167116	test-rmse:2.44536+0.0270448
[12]	train-rmse:2.18587+0.0140429	test-rmse:2.41126+0.0286575
[13]	train-rmse:2.15048+0.0173978	test-rmse:2.38239+0.0277577
[14]	train-rmse:2.12392+0.0147335	test-rmse:2.36112+0.0224112
[15]	train-rmse:2.08941+0.0146762	test-rmse:2.33325+0.0231043
[16]	train-rmse:2.066

[133]	train-rmse:1.15874+0.0208739	test-rmse:1.67285+0.0334333
[134]	train-rmse:1.15608+0.0216448	test-rmse:1.67162+0.0328617
[135]	train-rmse:1.15266+0.0198882	test-rmse:1.66977+0.0339027
[136]	train-rmse:1.14955+0.0206424	test-rmse:1.66769+0.034402
[137]	train-rmse:1.14704+0.0200624	test-rmse:1.66585+0.0349154
[138]	train-rmse:1.14341+0.0199864	test-rmse:1.66362+0.0352725
[139]	train-rmse:1.14006+0.0198722	test-rmse:1.66141+0.0357857
[140]	train-rmse:1.13521+0.0191492	test-rmse:1.65828+0.0359577
[141]	train-rmse:1.13203+0.0194557	test-rmse:1.65672+0.0361512
[142]	train-rmse:1.12934+0.0198311	test-rmse:1.65517+0.036449
[143]	train-rmse:1.12706+0.0209612	test-rmse:1.65421+0.036153
[144]	train-rmse:1.12523+0.0210528	test-rmse:1.65315+0.0364729
[145]	train-rmse:1.12187+0.0209357	test-rmse:1.65127+0.0362524
[146]	train-rmse:1.11911+0.0207823	test-rmse:1.64941+0.0365453
[147]	train-rmse:1.11653+0.0207298	test-rmse:1.6477+0.0363732
[148]	train-rmse:1.11395+0.0215438	test-rmse:1.64647+0.0362

KeyboardInterrupt: 

In [12]:
params = {'objective':'reg:linear','eval_metric':'rmse' ,'max_depth':9,'min_child_weight':5,'tree_method':'gpu_hist'}

#xgtrain = xgb.DMatrix(train_X,label=train_y)
#xgtest = xgb.DMatrix(test_df)
watchlist=[(xgtrain,'train')]

bst=xgb.train(params,dtrain=xgtrain,num_boost_round=2000,evals=watchlist)
test_predictions = bst.predict(xgtest) 

[0]	train-rmse:7.23341
[1]	train-rmse:5.54345
[2]	train-rmse:4.40091
[3]	train-rmse:3.65535
[4]	train-rmse:3.18219
[5]	train-rmse:2.85317
[6]	train-rmse:2.6522
[7]	train-rmse:2.5076
[8]	train-rmse:2.40211
[9]	train-rmse:2.31401
[10]	train-rmse:2.24621
[11]	train-rmse:2.20381
[12]	train-rmse:2.15243
[13]	train-rmse:2.12559
[14]	train-rmse:2.10907
[15]	train-rmse:2.08654
[16]	train-rmse:2.065
[17]	train-rmse:2.04854
[18]	train-rmse:2.03394
[19]	train-rmse:2.0159
[20]	train-rmse:2.0016
[21]	train-rmse:1.97014
[22]	train-rmse:1.95818
[23]	train-rmse:1.93028
[24]	train-rmse:1.91147
[25]	train-rmse:1.8876
[26]	train-rmse:1.87742
[27]	train-rmse:1.86201
[28]	train-rmse:1.85315
[29]	train-rmse:1.83937
[30]	train-rmse:1.8255
[31]	train-rmse:1.81607
[32]	train-rmse:1.8099
[33]	train-rmse:1.79308
[34]	train-rmse:1.78136
[35]	train-rmse:1.76543
[36]	train-rmse:1.75644
[37]	train-rmse:1.74954
[38]	train-rmse:1.73768
[39]	train-rmse:1.71732
[40]	train-rmse:1.70488
[41]	train-rmse:1.69823
[42]	train-

[329]	train-rmse:0.81022
[330]	train-rmse:0.809402
[331]	train-rmse:0.809214
[332]	train-rmse:0.808712
[333]	train-rmse:0.807661
[334]	train-rmse:0.805727
[335]	train-rmse:0.805015
[336]	train-rmse:0.804069
[337]	train-rmse:0.803413
[338]	train-rmse:0.802661
[339]	train-rmse:0.801498
[340]	train-rmse:0.801229
[341]	train-rmse:0.800887
[342]	train-rmse:0.800811
[343]	train-rmse:0.800505
[344]	train-rmse:0.800243
[345]	train-rmse:0.799635
[346]	train-rmse:0.799065
[347]	train-rmse:0.797766
[348]	train-rmse:0.797377
[349]	train-rmse:0.797135
[350]	train-rmse:0.796753
[351]	train-rmse:0.795481
[352]	train-rmse:0.794122
[353]	train-rmse:0.793087
[354]	train-rmse:0.792102
[355]	train-rmse:0.791188
[356]	train-rmse:0.78992
[357]	train-rmse:0.789036
[358]	train-rmse:0.788525
[359]	train-rmse:0.787048
[360]	train-rmse:0.786505
[361]	train-rmse:0.78626
[362]	train-rmse:0.78614
[363]	train-rmse:0.785481
[364]	train-rmse:0.784783
[365]	train-rmse:0.783575
[366]	train-rmse:0.78312
[367]	train-rmse:

[646]	train-rmse:0.617468
[647]	train-rmse:0.617005
[648]	train-rmse:0.616747
[649]	train-rmse:0.616283
[650]	train-rmse:0.615538
[651]	train-rmse:0.615293
[652]	train-rmse:0.61502
[653]	train-rmse:0.614886
[654]	train-rmse:0.614674
[655]	train-rmse:0.61404
[656]	train-rmse:0.613266
[657]	train-rmse:0.612766
[658]	train-rmse:0.612293
[659]	train-rmse:0.611949
[660]	train-rmse:0.611622
[661]	train-rmse:0.61144
[662]	train-rmse:0.611274
[663]	train-rmse:0.61111
[664]	train-rmse:0.610828
[665]	train-rmse:0.610741
[666]	train-rmse:0.610217
[667]	train-rmse:0.610049
[668]	train-rmse:0.609791
[669]	train-rmse:0.609463
[670]	train-rmse:0.609062
[671]	train-rmse:0.608847
[672]	train-rmse:0.608678
[673]	train-rmse:0.60803
[674]	train-rmse:0.60765
[675]	train-rmse:0.607374
[676]	train-rmse:0.607174
[677]	train-rmse:0.606977
[678]	train-rmse:0.606382
[679]	train-rmse:0.606037
[680]	train-rmse:0.605799
[681]	train-rmse:0.605591
[682]	train-rmse:0.605252
[683]	train-rmse:0.604589
[684]	train-rmse:0

[963]	train-rmse:0.535737
[964]	train-rmse:0.535485
[965]	train-rmse:0.535224
[966]	train-rmse:0.535142
[967]	train-rmse:0.535007
[968]	train-rmse:0.534833
[969]	train-rmse:0.534732
[970]	train-rmse:0.534593
[971]	train-rmse:0.534371
[972]	train-rmse:0.534207
[973]	train-rmse:0.534114
[974]	train-rmse:0.53397
[975]	train-rmse:0.533837
[976]	train-rmse:0.533612
[977]	train-rmse:0.53359
[978]	train-rmse:0.533542
[979]	train-rmse:0.53344
[980]	train-rmse:0.533402
[981]	train-rmse:0.533361
[982]	train-rmse:0.533248
[983]	train-rmse:0.533008
[984]	train-rmse:0.532892
[985]	train-rmse:0.532677
[986]	train-rmse:0.532549
[987]	train-rmse:0.532251
[988]	train-rmse:0.531838
[989]	train-rmse:0.531747
[990]	train-rmse:0.531434
[991]	train-rmse:0.531382
[992]	train-rmse:0.531287
[993]	train-rmse:0.531123
[994]	train-rmse:0.530757
[995]	train-rmse:0.530541
[996]	train-rmse:0.530149
[997]	train-rmse:0.529999
[998]	train-rmse:0.529921
[999]	train-rmse:0.529721
[1000]	train-rmse:0.529467
[1001]	train-r

[1270]	train-rmse:0.497054
[1271]	train-rmse:0.496993
[1272]	train-rmse:0.496949
[1273]	train-rmse:0.496861
[1274]	train-rmse:0.496727
[1275]	train-rmse:0.496651
[1276]	train-rmse:0.496469
[1277]	train-rmse:0.496392
[1278]	train-rmse:0.496302
[1279]	train-rmse:0.496242
[1280]	train-rmse:0.496126
[1281]	train-rmse:0.495981
[1282]	train-rmse:0.495864
[1283]	train-rmse:0.495662
[1284]	train-rmse:0.495532
[1285]	train-rmse:0.495339
[1286]	train-rmse:0.495233
[1287]	train-rmse:0.495178
[1288]	train-rmse:0.495093
[1289]	train-rmse:0.495053
[1290]	train-rmse:0.494899
[1291]	train-rmse:0.494885
[1292]	train-rmse:0.494847
[1293]	train-rmse:0.494824
[1294]	train-rmse:0.494639
[1295]	train-rmse:0.494524
[1296]	train-rmse:0.494471
[1297]	train-rmse:0.494427
[1298]	train-rmse:0.494273
[1299]	train-rmse:0.494258
[1300]	train-rmse:0.494182
[1301]	train-rmse:0.494071
[1302]	train-rmse:0.493948
[1303]	train-rmse:0.493888
[1304]	train-rmse:0.493834
[1305]	train-rmse:0.493709
[1306]	train-rmse:0.493523
[

[1575]	train-rmse:0.472259
[1576]	train-rmse:0.47224
[1577]	train-rmse:0.472186
[1578]	train-rmse:0.472107
[1579]	train-rmse:0.472004
[1580]	train-rmse:0.471895
[1581]	train-rmse:0.471805
[1582]	train-rmse:0.471762
[1583]	train-rmse:0.471735
[1584]	train-rmse:0.471635
[1585]	train-rmse:0.471439
[1586]	train-rmse:0.471402
[1587]	train-rmse:0.471349
[1588]	train-rmse:0.47132
[1589]	train-rmse:0.471287
[1590]	train-rmse:0.471185
[1591]	train-rmse:0.47114
[1592]	train-rmse:0.471072
[1593]	train-rmse:0.471059
[1594]	train-rmse:0.471049
[1595]	train-rmse:0.470984
[1596]	train-rmse:0.470973
[1597]	train-rmse:0.47091
[1598]	train-rmse:0.470841
[1599]	train-rmse:0.470807
[1600]	train-rmse:0.470731
[1601]	train-rmse:0.470678
[1602]	train-rmse:0.470642
[1603]	train-rmse:0.470601
[1604]	train-rmse:0.470585
[1605]	train-rmse:0.470566
[1606]	train-rmse:0.470512
[1607]	train-rmse:0.470487
[1608]	train-rmse:0.470417
[1609]	train-rmse:0.470374
[1610]	train-rmse:0.47034
[1611]	train-rmse:0.470234
[1612]

[1880]	train-rmse:0.456516
[1881]	train-rmse:0.456479
[1882]	train-rmse:0.456472
[1883]	train-rmse:0.456412
[1884]	train-rmse:0.456366
[1885]	train-rmse:0.456294
[1886]	train-rmse:0.456269
[1887]	train-rmse:0.456194
[1888]	train-rmse:0.456142
[1889]	train-rmse:0.456104
[1890]	train-rmse:0.456059
[1891]	train-rmse:0.455969
[1892]	train-rmse:0.455933
[1893]	train-rmse:0.455883
[1894]	train-rmse:0.455826
[1895]	train-rmse:0.455798
[1896]	train-rmse:0.455762
[1897]	train-rmse:0.455749
[1898]	train-rmse:0.455705
[1899]	train-rmse:0.455652
[1900]	train-rmse:0.4556
[1901]	train-rmse:0.455553
[1902]	train-rmse:0.455542
[1903]	train-rmse:0.455507
[1904]	train-rmse:0.455449
[1905]	train-rmse:0.455375
[1906]	train-rmse:0.455364
[1907]	train-rmse:0.455341
[1908]	train-rmse:0.455297
[1909]	train-rmse:0.455216
[1910]	train-rmse:0.455146
[1911]	train-rmse:0.455109
[1912]	train-rmse:0.455093
[1913]	train-rmse:0.455079
[1914]	train-rmse:0.455069
[1915]	train-rmse:0.455063
[1916]	train-rmse:0.455005
[19

In [13]:
test_df = pd.read_csv('test.csv')  
id1=test_df.id
id1['price']=test_predictions

sp = pd.DataFrame()
sp['id']=id1
sp.drop(sp.index[-1],inplace=True)
sp['price']=test_predictions
sp.to_csv('try.csv',index=False)
d=pd.read_csv('try.csv')
print(d)

          id      price
0          1   4.323555
1          2   6.026837
2          3  14.143586
3          4   5.804636
4          5   4.835774
5          6   6.736618
6          7   9.834146
7          8   3.585647
8          9   8.442663
9         10   6.125823
10        11   5.803451
11        12   9.517125
12        13   3.962944
13        14   7.572514
14        15   7.194418
15        16  11.492068
16        17   6.674393
17        18   5.488845
18        19   7.627204
19        20   4.965589
20        21   4.113758
21        22   6.226323
22        23   7.758048
23        24   5.729409
24        25   8.351530
25        26   5.427945
26        27   4.261944
27        28   2.439570
28        29   7.841132
29        30   3.423980
...      ...        ...
56249  57970   4.003297
56250  57971   6.194546
56251  57973   6.920943
56252  57974   8.518730
56253  57975   8.565639
56254  57976  12.965111
56255  57977   6.707685
56256  57978   5.905424
56257  57979   4.948421
56258  57980  11

c:\users\王泽灏\appdata\local\programs\python\python36\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [ ]:
param_test1 = {
 'max_depth':range(3,10,2),
# 'min_child_weight':range(1,6,2)
}
gsearch1 = GridSearchCV(estimator = XGBClassifier(learning_rate =0.3, n_estimators=10,), 
 param_grid = param_test1,  scoring='neg_mean_squared_error',iid=True, cv=5,verbose=2)
gsearch1.fit(train_X,train_y)
gsearch1.grid_scores_, gsearch1.best_params_,     gsearch1.best_score_
print_best_score(gsearch,param_test)

Fitting 5 folds for each of 4 candidates, totalling 20 fits
[CV] max_depth=3 .....................................................


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] ...................................... max_depth=3, total=11.4min
[CV] max_depth=3 .....................................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed: 14.7min remaining:    0.0s


In [ ]:
param_test1 = {
 'max_depth':range(3,10,2),
 'min_child_weight':range(1,6,2)
}
gsearch1 = GridSearchCV(estimator = XGBClassifier(learning_rate =0.3, n_estimators=500, max_depth=5,
min_child_weight=1, gamma=0, subsample=0.8,             colsample_bytree=0.8,
 objective= 'gpu::reg:linear', nthread=4, seed=27,kvargs={'tree_method':'gpu_hist'}), 
 param_grid = param_test1,  scoring='neg_mean_squared_error',n_jobs=4,iid=True, cv=5,n_jobs=-1)
gsearch1.fit(train_X,train_y)
gsearch1.grid_scores_, gsearch1.best_params_,     gsearch1.best_score_
